In [1]:
import random
random.seed(42)

## spark imports
from pyspark.sql import Row, SparkSession
from pyspark.sql.functions import *
from pyspark.sql.functions import isnan, when, count, col
import pandas as pd

from pyspark import SparkContext
from pyspark.sql import SQLContext

from pyspark.sql import SparkSession

from pyspark.ml import feature
from pyspark.sql.functions import udf
# Import necessary libraries
from pyspark.sql import *
from pyspark.sql.functions import *
from pyspark.ml.regression import LinearRegression
from pyspark.ml.linalg import Vectors
from pyspark.ml.feature import *
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.sql.functions import abs, sqrt
from pyspark.sql.types import IntegerType
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

In [2]:
# Databricks notebook source
# import data and drop unwanted columns

from pyspark.sql import SQLContext
sqlContext = SQLContext(sc)
df = sqlContext.sql("SELECT * FROM listings_new_csv")
display(df)

id listing_url scrape_id last_scraped name summary space description experiences_offered neighborhood_overview notes transit access interaction house_rules thumbnail_url medium_url picture_url xl_picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified street neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed city state zipcode market smart_location country_code country latitude longitude is_location_exact property_type room_type accommodates bathrooms bedrooms beds bed_type amenities square_feet price weekly_price monthly_price security_deposit cleaning_fee guests_included extra_people minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value requires_license license jurisdiction_names instant_bookable is_business_travel_ready cancellation_policy require_guest_profile_picture require_guest_phone_verification calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 1419 https://www.airbnb.com/rooms/1419 20190506125802 2019-05-06T00:00:00.000+0000 Beautiful home in amazing area! This large, family home is located in one of Toronto's most vibrant downtown neighbourhoods. The five-bedroom, three-bath house is newly renovated and complete with all the amenities you'll need for a fabulous time in the city. Visit Toronto with this fabulous furnished home as your base! This lovely home is surrounded by gardens in the back and front. Inside, you'll find a large open space with a modern kitchen and bright living and dining room. There are two floors up - a master bedroom with a king-size bed and two kids rooms, each with a single bed. The attic is a private space with a king-sized bed, fold-out single couch and a private deck. The basement is fully-finished with a private room and bath, as well as a playroom with another single couch that doubles as a sleeping space. The house will comfortably sleep 10. For kids of all ages: we have toys, a very cool tree fort, and many great parks and playgrounds nearby. This large, family home is located in one of Toronto's most vibrant downtown neighbourhoods. The five-bedroom, three-bath house is newly renovated and complete with all the amenities you'll need for a fabulous time in the city. Visit Toronto with this fabulous furnished home as your base! This lovely home is surrounded by gardens in the back and front. Inside, you'll find a large open space with a modern kitchen and bright living and dining room. There are two floors up - a master bedroom with a king-size bed and two kids rooms, each with a single bed. The attic is a private space with a king-sized bed, fold-out single couch and a private deck. The basement is fully-finished with a private room and bath, as well as a playroom with another single couch that doubles as a sleeping space. The house will comfortably sleep 10. For kids of all ages: we have toys, a very cool tree fort, and many great parks and playgrounds nearby. The whole house and garden are available. We will be out of to none The apartment is located in the Ossington strip between Dundas and Queen, a fabulous, family-friendly and incredibly fun area with amazing restaurants, cafes and shops. It is considered one of Toronto's best

In [3]:
df.count()

Out[ 414 ]: 20303

In [4]:
#As this file has 95 columns, I decide to have a look at the features names to delete the ones that directly seem useless.
#This is my first feature selection step.

useless =  ['id','listing_url', 'scrape_id', 'last_scraped','name', 'summary', 'space', 'description', 'experiences_offered',
                  'neighborhood_overview', 'notes', 'transit', 'access', 'interaction', 'thumbnail_url','medium_url', 'picture_url',
                  'xl_picture_url', 'host_id', 'host_url', 'host_name', 'host_since', 'host_location', 'host_about', 'host_response_time',
                  'host_response_rate', 'host_acceptance_rate', 'host_is_superhost', 'host_thumbnail_url', 'host_picture_url', 'host_listings_count',
                  'host_total_listings_count','host_verifications', 'host_has_profile_pic', 'host_identity_verified','street', 'neighbourhood_group_cleansed',
                  'city','state','market', 'smart_location','country_code','country','latitude', 'longitude', 'is_location_exact','weekly_price',
                  'monthly_price','minimum_nights', 'maximum_nights', 'minimum_minimum_nights', 'maximum_minimum_nights', 'minimum_maximum_nights',
                  'maximum_maximum_nights', 'calendar_updated', 'has_availability','availability_30','availability_60','availability_90', 
                  'availability_365','calendar_last_scraped', 'number_of_reviews', 'number_of_reviews_ltm', 'first_review', 'last_review',
                  'review_scores_rating','review_scores_accuracy','review_scores_cleanliness', 'review_scores_checkin', 'review_scores_communication',
                  'review_Scores_location', 'review_Scores_value', 'license', 'jurisdiction_names',  'requires_guest_profile',
                  'requires_guest_phone_verification','calculated_host_listings_count', 'calculated_host_listings_count_entire_homes','calculated_host_listings_count_private_rooms',
                  'calculated_host_listings_count_shared_rooms','reviews_per_month', 'host_neighbourhood', 'neighbourhood', 'zipcode','requires_license',
                   'is_business_travel_ready', 'require_guest_profile_picture', 'require_guest_phone_verification', 'extra_people', 'guests_included']
data = df.drop(*useless)


display(data)

house_rules neighbourhood_cleansed property_type room_type accommodates bathrooms bedrooms beds bed_type amenities square_feet price security_deposit cleaning_fee minimum_nights_avg_ntm maximum_nights_avg_ntm instant_bookable cancellation_policy This is our much-loved family home. We expect guests to treat it with respect, as they would their own. This is a quiet neighbourhood and we respect our neighbours. As such, no parties or events are permitted and the reservation will be immediately cancelled with funds forfeited should one occur. Little Portugal House Entire home/apt 10 3.0 5 7 Real Bed {TV,Internet,Wifi,"Air conditioning",Kitchen,"Indoor fireplace",Heating,"Family/kid friendly",Washer,Dryer,"Smoke detector","First aid kit","Fire extinguisher",Essentials,Shampoo} 1400 $469.00 $1,000.00 $150.00 4.0 730.0 f strict_14_with_grace_period No smoking please. Waterfront Communities-The Island Apartment Private room 2 1.5 1 1 Real Bed {TV,"Cable TV",Internet,Wifi,"Air conditioning",Pool,"Free parking on premises",Doorman,Gym,Elevator,"Buzzer/wireless intercom",Heating,"Smoke detector",Shampoo} null $101.00 $2,693.00 null 180.0 365.0 t strict_14_with_grace_period no smoking Annex House Private room 1 1.5 1 1 Pull-out Sofa {Internet,Wifi,"Pets live on this property",Cat(s),"Indoor fireplace"} 120 $67.00 $134.00 $27.00 1.0 10.0 f moderate * Guests are requested to leave their shoes at the main entrance of our home to help keep the house clean. * Guests are welcome to come and go as they please, provided they share what their initial time of arrival and time of departure on the final day of their stay with us will be. * Guests are requested to let us know in advance if they will require a taxi ride to the airport to allow for smooth planning. * Guests are welcome to extend their stay with minimal notice, as long as the room is not booked by other guests or being used to host family. * Guests are requested not to let anyone into our home without letting us know in advance. Briar Hill-Belgravia House Private room 3 1.0 1 1 Real Bed {Internet,Wifi,"Air conditioning",Kitchen,"Free parking on premises","Free street parking",Heating,Washer,Dryer,"Smoke detector","Carbon monoxide detector","Fire extinguisher",Essentials,"Lock on bedroom door","24-hour check-in",Hangers,"Hair dryer",Iron,"Laptop friendly workspace","translation missing: en.hosting_amenity_49","translation missing: en.hosting_amenity_50","Self check-in",Keypad,"Private entrance","Hot water","Bed linens","Extra pillows and blankets","Pocket wifi",Microwave,"Coffee maker",Refrigerator,"Dishes and silverware","Cooking basics",Oven,Stove,"Long term stays allowed","Step-free access"} null $73.00 $0.00 $0.00 1.0 28.0 t strict_14_with_grace_period No Smoking. This unit is suitable for one guest only. However, visitors are welcome. Greenwood-Coxwell Apartment Entire home/apt 1 1.0 0 1 Real Bed {TV,Internet,Wifi,"Air conditioning",Kitchen,"Free parking on premises","Pets live on this property",Dog(s),Heating,Washer,Dryer,"Smoke detector","Carbon monoxide detector","Fire extinguisher",Hangers,Iron,"Laptop friendly workspace","translation missing: en.hosting_amenity_49"} null $54.00 null null 120.0 365.0 f strict_14_with_grace_period null Waterfront Communities-The Island Apartment Entire home/apt 2 1.5 1 2 Real Bed {TV,"Cable TV",Internet,Wifi,"Air conditioning",Pool,Kitchen,"Free parking on premises",Doorman,Gym,Elevator,Heating,"Smoke detector"} 1050 $135.00 $4,040.00 null 180.0 365.0 f strict_14_with_grace_period -----------------IMPORTANT------------------------------------------ INSTANT BOOKING FOR Guests who have received positive reviews from hosts. Guests are responsible to obey house rules and it will be guests responsibity for damages caused by guests. 1-Mattresses protected by matress covers. They can not be removed by guests during their stay. If a mattress is stained, the warranty is void so it will be guests responsibility if they are stained. 2- The kitchen has granite

In [5]:
neighbourhood_df = sqlContext.sql("SELECT * FROM wellbeing_toronto_csv").drop("Combined_Indicators", "Neighbourhood_ID")

# join the listings with the wellbeing neighbourhood data by neighbourhood name
airbnb_df = data.join(neighbourhood_df, data.neighbourhood_cleansed == neighbourhood_df.Neighbourhood).drop("Neighbourhood", "neighbourhood_cleansed", "Neighbourhood_ID")

In [6]:
tokenizer = RegexTokenizer(inputCol="amenities", outputCol="amenitieslist", pattern="\\W+")
tokenized = tokenizer.transform(airbnb_df)

hashingTF = HashingTF(inputCol=tokenizer.getOutputCol(), outputCol="amenitiesFeatures", numFeatures=40)
airbnb_df = hashingTF.transform(tokenized).drop("amenities", "amenitieslist")

In [7]:
len(airbnb_df.columns)

Out[ 418 ]: 29

In [8]:
display(airbnb_df)

house_rules property_type room_type accommodates bathrooms bedrooms beds bed_type square_feet price security_deposit cleaning_fee minimum_nights_avg_ntm maximum_nights_avg_ntm instant_bookable cancellation_policy Total_Population Low_Income_Lone_Parent_Families Average_Family_Income Visible_Minority_Category Not_Visible_Minority Recent_Immigrants College_Certificate/Diploma Bachelor_Degree_or_Higher Tenant_Average_Rent Unemployed Low_Income_Families Total_Area amenitiesFeatures This is our much-loved family home. We expect guests to treat it with respect, as they would their own. This is a quiet neighbourhood and we respect our neighbours. As such, no parties or events are permitted and the reservation will be immediately cancelled with funds forfeited should one occur. House Entire home/apt 10 3.0 5 7 Real Bed 1400 $469.00 $1,000.00 $150.00 4.0 730.0 f strict_14_with_grace_period 15559 200 74372 15055 10790 500 8490 5840 997 685 1300 1.2 List(0, 40, List(3, 5, 8, 10, 12, 13, 14, 15, 17, 18, 21, 23, 24, 26, 29, 31, 33, 34, 36, 38, 39), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0, 1.0, 1.0)) No smoking please. Apartment Private room 2 1.5 1 1 Real Bed null $101.00 $2,693.00 null 180.0 365.0 t strict_14_with_grace_period 65913 410 95004 65620 36715 4730 51740 41735 1417 2640 4480 7.6 List(0, 40, List(1, 2, 3, 5, 8, 10, 18, 20, 21, 23, 25, 26, 28, 31, 33, 34, 36, 38), List(1.0, 2.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0)) no smoking House Private room 1 1.5 1 1 Pull-out Sofa 120 $67.00 $134.00 $27.00 1.0 10.0 f moderate 30526 230 141111 28640 21380 975 20430 16590 1237 1250 3110 2.8 List(0, 40, List(2, 8, 12, 13, 16, 17, 36, 37), List(1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 2.0)) * Guests are requested to leave their shoes at the main entrance of our home to help keep the house clean. * Guests are welcome to come and go as they please, provided they share what their initial time of arrival and time of departure on the final day of their stay with us will be. * Guests are requested to let us know in advance if they will require a taxi ride to the airport to allow for smooth planning. * Guests are welcome to extend their stay with minimal notice, as long as the room is not booked by other guests or being used to host family. * Guests are requested not to let anyone into our home without letting us know in advance. House Private room 3 1.0 1 1 Real Bed null $73.00 $0.00 $0.00 1.0 28.0 t strict_14_with_grace_period 14257 250 67358 14205 7710 1425 6730 3405 976 725 1670 1.8 List(0, 40, List(2, 3, 5, 7, 8, 9, 10, 11, 12, 13, 14, 16, 18, 19, 21, 23, 24, 25, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 38, 39), List(6.0, 6.0, 5.0, 3.0, 4.0, 1.0, 1.0, 1.0, 1.0, 3.0, 3.0, 2.0, 2.0, 1.0, 1.0, 4.0, 5.0, 1.0, 1.0, 2.0, 3.0, 3.0, 3.0, 1.0, 5.0, 2.0, 1.0, 3.0, 3.0, 3.0)) No Smoking. This unit is suitable for one guest only. However, visitors are welcome. Apartment Entire home/apt 1 1.0 0 1 Real Bed null $54.00 null null 120.0 365.0 f strict_14_with_grace_period 14417 260 76085 14380 8755 335 7255 4590 829 595 1610 1.7 List(0, 40, List(2, 3, 5, 7, 8, 9, 10, 11, 13, 14, 18, 21, 23, 24, 29, 31, 32, 33, 34, 36, 37, 38, 39), List(2.0, 3.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 2.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 2.0, 2.0, 2.0)) null Apartment Entire home/apt 2 1.5 1 2 Real Bed 1050 $135.00 $4,040.00 null 180.0 365.0 f strict_14_with_grace_period 65913 410 95004 65620 36715 4730 51740 41735 1417 2640 4480 7.6 List(0, 40, List(2, 3, 5, 8, 10, 18, 20, 21, 23, 25, 31, 33, 34, 36, 38), List(2.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0)) -----------------IMPORTANT------------------------------------------ INSTANT BOOKING FOR Guests who have received positive reviews from hosts. Guests are responsible to obey house rules and it will be guests responsibity for damages caused by guests. 1-Mattresses protected by matress covers. 

In [9]:
# Replace a characther in a string 
def replace_char(df,column_name,orig_char, new_char):
  return(df.withColumn(column_name, regexp_replace(column_name,orig_char,new_char)))

In [10]:
airbnb_df = replace_char(airbnb_df,"property_type"," ","_")
airbnb_df = replace_char(airbnb_df, "room_type"," ","_")
airbnb_df = replace_char(airbnb_df, "bed_type", " ", "_")

In [11]:
#Check if data in cell, if no data present return 0 else 1
def true_false_categorization(text):
  if text != None:
    return (1)
  else:
    return(0)

In [12]:
udf_recode_true_false = udf(true_false_categorization)
airbnb_df = airbnb_df.withColumn('house_rules', udf_recode_true_false('house_rules'))
display(airbnb_df)

house_rules property_type room_type accommodates bathrooms bedrooms beds bed_type square_feet price security_deposit cleaning_fee minimum_nights_avg_ntm maximum_nights_avg_ntm instant_bookable cancellation_policy Total_Population Low_Income_Lone_Parent_Families Average_Family_Income Visible_Minority_Category Not_Visible_Minority Recent_Immigrants College_Certificate/Diploma Bachelor_Degree_or_Higher Tenant_Average_Rent Unemployed Low_Income_Families Total_Area amenitiesFeatures 1 House Entire_home/apt 10 3.0 5 7 Real_Bed 1400 $469.00 $1,000.00 $150.00 4.0 730.0 f strict_14_with_grace_period 15559 200 74372 15055 10790 500 8490 5840 997 685 1300 1.2 List(0, 40, List(3, 5, 8, 10, 12, 13, 14, 15, 17, 18, 21, 23, 24, 26, 29, 31, 33, 34, 36, 38, 39), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0, 1.0, 1.0)) 1 Apartment Private_room 2 1.5 1 1 Real_Bed null $101.00 $2,693.00 null 180.0 365.0 t strict_14_with_grace_period 65913 410 95004 65620 36715 4730 51740 41735 1417 2640 4480 7.6 List(0, 40, List(1, 2, 3, 5, 8, 10, 18, 20, 21, 23, 25, 26, 28, 31, 33, 34, 36, 38), List(1.0, 2.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0)) 1 House Private_room 1 1.5 1 1 Pull-out_Sofa 120 $67.00 $134.00 $27.00 1.0 10.0 f moderate 30526 230 141111 28640 21380 975 20430 16590 1237 1250 3110 2.8 List(0, 40, List(2, 8, 12, 13, 16, 17, 36, 37), List(1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 2.0)) 1 House Private_room 3 1.0 1 1 Real_Bed null $73.00 $0.00 $0.00 1.0 28.0 t strict_14_with_grace_period 14257 250 67358 14205 7710 1425 6730 3405 976 725 1670 1.8 List(0, 40, List(2, 3, 5, 7, 8, 9, 10, 11, 12, 13, 14, 16, 18, 19, 21, 23, 24, 25, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 38, 39), List(6.0, 6.0, 5.0, 3.0, 4.0, 1.0, 1.0, 1.0, 1.0, 3.0, 3.0, 2.0, 2.0, 1.0, 1.0, 4.0, 5.0, 1.0, 1.0, 2.0, 3.0, 3.0, 3.0, 1.0, 5.0, 2.0, 1.0, 3.0, 3.0, 3.0)) 1 Apartment Entire_home/apt 1 1.0 0 1 Real_Bed null $54.00 null null 120.0 365.0 f strict_14_with_grace_period 14417 260 76085 14380 8755 335 7255 4590 829 595 1610 1.7 List(0, 40, List(2, 3, 5, 7, 8, 9, 10, 11, 13, 14, 18, 21, 23, 24, 29, 31, 32, 33, 34, 36, 37, 38, 39), List(2.0, 3.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 2.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 2.0, 2.0, 2.0)) 0 Apartment Entire_home/apt 2 1.5 1 2 Real_Bed 1050 $135.00 $4,040.00 null 180.0 365.0 f strict_14_with_grace_period 65913 410 95004 65620 36715 4730 51740 41735 1417 2640 4480 7.6 List(0, 40, List(2, 3, 5, 8, 10, 18, 20, 21, 23, 25, 31, 33, 34, 36, 38), List(2.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0)) 1 House Entire_home/apt 5 1.0 2 2 Real_Bed null $150.00 $750.00 $125.00 37.1 365.0 f strict_14_with_grace_period 21849 440 54454 20655 10730 1695 11020 5900 865 1125 3640 2.3 List(0, 40, List(2, 3, 4, 5, 7, 8, 9, 10, 11, 12, 13, 14, 18, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 36, 38, 39), List(3.0, 6.0, 1.0, 3.0, 1.0, 2.0, 1.0, 2.0, 1.0, 1.0, 2.0, 3.0, 2.0, 1.0, 1.0, 3.0, 2.0, 1.0, 1.0, 1.0, 2.0, 2.0, 2.0, 2.0, 2.0, 4.0, 2.0, 1.0, 2.0, 2.0)) 1 Apartment Entire_home/apt 2 1.0 0 1 Real_Bed 300 $68.00 null $40.00 2.0 730.0 t moderate 13845 420 50793 13610 3365 1760 5470 2950 730 900 2570 1.8 List(0, 40, List(2, 3, 7, 8, 11, 13, 14, 18, 21, 23, 24, 29, 30, 31, 33, 36, 37, 38, 39), List(2.0, 2.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 2.0, 2.0, 1.0)) 1 Bungalow Entire_home/apt 4 1.0 2 2 Real_Bed 100 $110.00 $150.00 $0.00 2.0 90.0 t moderate 27917 470 69418 27545 12270 1970 11710 5305 904 1285 2670 10.2 List(0, 40, List(1, 2, 3, 5, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 18, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 36, 37, 38, 39), List(2.0, 2.0, 4.0, 1.0, 2.0, 4.0, 1.0, 2.0, 1.0, 2.0, 5.0, 2.0, 2.0, 1.0, 2.0, 1.0, 1.0, 1.0, 4.0, 4.0, 1.0, 1.0, 2.0, 2.0, 5.0, 2.0, 3.0, 2.0, 5.0, 3.0, 4.0, 3.0, 1.0, 3.0)) 1 Apartment Entire_home/apt 2 1.0 1 1 Real_Bed null $119.00 $0.

In [13]:
airbnb_df.count()

Out[ 424 ]: 19421

In [14]:
list = ['property_type', 'bed_type']

airbnb_df = airbnb_df.dropna(subset=list)

display(airbnb_df)

house_rules property_type room_type accommodates bathrooms bedrooms beds bed_type square_feet price security_deposit cleaning_fee minimum_nights_avg_ntm maximum_nights_avg_ntm instant_bookable cancellation_policy Total_Population Low_Income_Lone_Parent_Families Average_Family_Income Visible_Minority_Category Not_Visible_Minority Recent_Immigrants College_Certificate/Diploma Bachelor_Degree_or_Higher Tenant_Average_Rent Unemployed Low_Income_Families Total_Area amenitiesFeatures 1 House Entire_home/apt 10 3.0 5 7 Real_Bed 1400 $469.00 $1,000.00 $150.00 4.0 730.0 f strict_14_with_grace_period 15559 200 74372 15055 10790 500 8490 5840 997 685 1300 1.2 List(0, 40, List(3, 5, 8, 10, 12, 13, 14, 15, 17, 18, 21, 23, 24, 26, 29, 31, 33, 34, 36, 38, 39), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0, 1.0, 1.0)) 1 Apartment Private_room 2 1.5 1 1 Real_Bed null $101.00 $2,693.00 null 180.0 365.0 t strict_14_with_grace_period 65913 410 95004 65620 36715 4730 51740 41735 1417 2640 4480 7.6 List(0, 40, List(1, 2, 3, 5, 8, 10, 18, 20, 21, 23, 25, 26, 28, 31, 33, 34, 36, 38), List(1.0, 2.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0)) 1 House Private_room 1 1.5 1 1 Pull-out_Sofa 120 $67.00 $134.00 $27.00 1.0 10.0 f moderate 30526 230 141111 28640 21380 975 20430 16590 1237 1250 3110 2.8 List(0, 40, List(2, 8, 12, 13, 16, 17, 36, 37), List(1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 2.0)) 1 House Private_room 3 1.0 1 1 Real_Bed null $73.00 $0.00 $0.00 1.0 28.0 t strict_14_with_grace_period 14257 250 67358 14205 7710 1425 6730 3405 976 725 1670 1.8 List(0, 40, List(2, 3, 5, 7, 8, 9, 10, 11, 12, 13, 14, 16, 18, 19, 21, 23, 24, 25, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 38, 39), List(6.0, 6.0, 5.0, 3.0, 4.0, 1.0, 1.0, 1.0, 1.0, 3.0, 3.0, 2.0, 2.0, 1.0, 1.0, 4.0, 5.0, 1.0, 1.0, 2.0, 3.0, 3.0, 3.0, 1.0, 5.0, 2.0, 1.0, 3.0, 3.0, 3.0)) 1 Apartment Entire_home/apt 1 1.0 0 1 Real_Bed null $54.00 null null 120.0 365.0 f strict_14_with_grace_period 14417 260 76085 14380 8755 335 7255 4590 829 595 1610 1.7 List(0, 40, List(2, 3, 5, 7, 8, 9, 10, 11, 13, 14, 18, 21, 23, 24, 29, 31, 32, 33, 34, 36, 37, 38, 39), List(2.0, 3.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 2.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 2.0, 2.0, 2.0)) 0 Apartment Entire_home/apt 2 1.5 1 2 Real_Bed 1050 $135.00 $4,040.00 null 180.0 365.0 f strict_14_with_grace_period 65913 410 95004 65620 36715 4730 51740 41735 1417 2640 4480 7.6 List(0, 40, List(2, 3, 5, 8, 10, 18, 20, 21, 23, 25, 31, 33, 34, 36, 38), List(2.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0)) 1 House Entire_home/apt 5 1.0 2 2 Real_Bed null $150.00 $750.00 $125.00 37.1 365.0 f strict_14_with_grace_period 21849 440 54454 20655 10730 1695 11020 5900 865 1125 3640 2.3 List(0, 40, List(2, 3, 4, 5, 7, 8, 9, 10, 11, 12, 13, 14, 18, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 36, 38, 39), List(3.0, 6.0, 1.0, 3.0, 1.0, 2.0, 1.0, 2.0, 1.0, 1.0, 2.0, 3.0, 2.0, 1.0, 1.0, 3.0, 2.0, 1.0, 1.0, 1.0, 2.0, 2.0, 2.0, 2.0, 2.0, 4.0, 2.0, 1.0, 2.0, 2.0)) 1 Apartment Entire_home/apt 2 1.0 0 1 Real_Bed 300 $68.00 null $40.00 2.0 730.0 t moderate 13845 420 50793 13610 3365 1760 5470 2950 730 900 2570 1.8 List(0, 40, List(2, 3, 7, 8, 11, 13, 14, 18, 21, 23, 24, 29, 30, 31, 33, 36, 37, 38, 39), List(2.0, 2.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 2.0, 2.0, 1.0)) 1 Bungalow Entire_home/apt 4 1.0 2 2 Real_Bed 100 $110.00 $150.00 $0.00 2.0 90.0 t moderate 27917 470 69418 27545 12270 1970 11710 5305 904 1285 2670 10.2 List(0, 40, List(1, 2, 3, 5, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 18, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 36, 37, 38, 39), List(2.0, 2.0, 4.0, 1.0, 2.0, 4.0, 1.0, 2.0, 1.0, 2.0, 5.0, 2.0, 2.0, 1.0, 2.0, 1.0, 1.0, 1.0, 4.0, 4.0, 1.0, 1.0, 2.0, 2.0, 5.0, 2.0, 3.0, 2.0, 5.0, 3.0, 4.0, 3.0, 1.0, 3.0)) 1 Apartment Entire_home/apt 2 1.0 1 1 Real_Bed null $119.00 $0.

In [15]:
one_list= ['property_type', 'room_type', 'bed_type', 'cancellation_policy']

airbnb_df.columns

Out[ 426 ]: 
['house_rules',
 'property_type',
 'room_type',
 'accommodates',
 'bathrooms',
 'bedrooms',
 'beds',
 'bed_type',
 'square_feet',
 'price',
 'security_deposit',
 'cleaning_fee',
 'minimum_nights_avg_ntm',
 'maximum_nights_avg_ntm',
 'instant_bookable',
 'cancellation_policy',
 'Total_Population',
 'Low_Income_Lone_Parent_Families',
 'Average_Family_Income',
 'Visible_Minority_Category',
 'Not_Visible_Minority',
 'Recent_Immigrants',
 'College_Certificate/Diploma',
 'Bachelor_Degree_or_Higher',
 'Tenant_Average_Rent',
 'Unemployed',
 'Low_Income_Families',
 'Total_Area\r',
 'amenitiesFeatures']

In [16]:
from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer, OneHotEncoder, VectorAssembler

indexers = [
    StringIndexer(inputCol=c, outputCol="{0}_indexed".format(c))
    for c in one_list
]

encoders = [
    OneHotEncoder(
        inputCol=indexer.getOutputCol(),
        outputCol="{0}_encoded".format(indexer.getOutputCol())) 
    for indexer in indexers
]




In [17]:
assembler = VectorAssembler(
    inputCols=[encoder.getOutputCol() for encoder in encoders],
    outputCol="features"
)

In [18]:
from pyspark.ml import Pipeline
pipeline = Pipeline(stages = indexers + encoders + [assembler])
final_df = pipeline.fit(airbnb_df).transform(airbnb_df)
#selectedCols = ['label', 'features'] + airbnb_df.columns


In [19]:
display(final_df)

house_rules property_type room_type accommodates bathrooms bedrooms beds bed_type square_feet price security_deposit cleaning_fee minimum_nights_avg_ntm maximum_nights_avg_ntm instant_bookable cancellation_policy Total_Population Low_Income_Lone_Parent_Families Average_Family_Income Visible_Minority_Category Not_Visible_Minority Recent_Immigrants College_Certificate/Diploma Bachelor_Degree_or_Higher Tenant_Average_Rent Unemployed Low_Income_Families Total_Area amenitiesFeatures property_type_indexed room_type_indexed bed_type_indexed cancellation_policy_indexed property_type_indexed_encoded room_type_indexed_encoded bed_type_indexed_encoded cancellation_policy_indexed_encoded features 1 House Entire_home/apt 10 3.0 5 7 Real_Bed 1400 $469.00 $1,000.00 $150.00 4.0 730.0 f strict_14_with_grace_period 15559 200 74372 15055 10790 500 8490 5840 997 685 1300 1.2 List(0, 40, List(3, 5, 8, 10, 12, 13, 14, 15, 17, 18, 21, 23, 24, 26, 29, 31, 33, 34, 36, 38, 39), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0, 1.0, 1.0)) 2.0 0.0 0.0 0.0 List(0, 28, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 4, List(0), List(1.0)) List(0, 4, List(0), List(1.0)) List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 1 Apartment Private_room 2 1.5 1 1 Real_Bed null $101.00 $2,693.00 null 180.0 365.0 t strict_14_with_grace_period 65913 410 95004 65620 36715 4730 51740 41735 1417 2640 4480 7.6 List(0, 40, List(1, 2, 3, 5, 8, 10, 18, 20, 21, 23, 25, 26, 28, 31, 33, 34, 36, 38), List(1.0, 2.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0)) 0.0 1.0 0.0 0.0 List(0, 28, List(0), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 4, List(0), List(1.0)) List(0, 4, List(0), List(1.0)) List(0, 38, List(0, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 1 House Private_room 1 1.5 1 1 Pull-out_Sofa 120 $67.00 $134.00 $27.00 1.0 10.0 f moderate 30526 230 141111 28640 21380 975 20430 16590 1237 1250 3110 2.8 List(0, 40, List(2, 8, 12, 13, 16, 17, 36, 37), List(1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 2.0)) 2.0 1.0 2.0 1.0 List(0, 28, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 4, List(2), List(1.0)) List(0, 4, List(1), List(1.0)) List(0, 38, List(2, 29, 32, 35), List(1.0, 1.0, 1.0, 1.0)) 1 House Private_room 3 1.0 1 1 Real_Bed null $73.00 $0.00 $0.00 1.0 28.0 t strict_14_with_grace_period 14257 250 67358 14205 7710 1425 6730 3405 976 725 1670 1.8 List(0, 40, List(2, 3, 5, 7, 8, 9, 10, 11, 12, 13, 14, 16, 18, 19, 21, 23, 24, 25, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 38, 39), List(6.0, 6.0, 5.0, 3.0, 4.0, 1.0, 1.0, 1.0, 1.0, 3.0, 3.0, 2.0, 2.0, 1.0, 1.0, 4.0, 5.0, 1.0, 1.0, 2.0, 3.0, 3.0, 3.0, 1.0, 5.0, 2.0, 1.0, 3.0, 3.0, 3.0)) 2.0 1.0 0.0 0.0 List(0, 28, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 4, List(0), List(1.0)) List(0, 4, List(0), List(1.0)) List(0, 38, List(2, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 1 Apartment Entire_home/apt 1 1.0 0 1 Real_Bed null $54.00 null null 120.0 365.0 f strict_14_with_grace_period 14417 260 76085 14380 8755 335 7255 4590 829 595 1610 1.7 List(0, 40, List(2, 3, 5, 7, 8, 9, 10, 11, 13, 14, 18, 21, 23, 24, 29, 31, 32, 33, 34, 36, 37, 38, 39), List(2.0, 3.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 2.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 2.0, 2.0, 2.0)) 0.0 0.0 0.0 0.0 List(0, 28, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 4, List(0), List(1.0)) List(0, 4, List(0), List(1.0)) List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 0 Apartment Entire_home/apt 2 1.5 1 2 Real_Bed 1050 $135.00 $4,040.00 null 180.0 365.0 f strict_14_with_grace_period 65913 410 95004 65620 36715 4730 51740 41735 1417 2640 4480 7.6 List(0, 40, List(2, 3, 5, 8, 10, 18, 20, 21, 23, 25, 31, 33, 34, 36, 38), List(2.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 2.0)) 0.0 0.0 0.0 0.0 List(0, 28, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 4, List(0), List(1.0)) List(0, 4, List(0), Lis

In [20]:
final_df.printSchema()
charReplace = udf(lambda x: x.replace('$',''))
final_df = final_df.withColumn('price', charReplace('price'))


root
-- house_rules: string (nullable = true)
-- property_type: string (nullable = true)
-- room_type: string (nullable = true)
-- accommodates: integer (nullable = true)
-- bathrooms: double (nullable = true)
-- bedrooms: integer (nullable = true)
-- beds: integer (nullable = true)
-- bed_type: string (nullable = true)
-- square_feet: integer (nullable = true)
-- price: string (nullable = true)
-- security_deposit: string (nullable = true)
-- cleaning_fee: string (nullable = true)
-- minimum_nights_avg_ntm: double (nullable = true)
-- maximum_nights_avg_ntm: double (nullable = true)
-- instant_bookable: string (nullable = true)
-- cancellation_policy: string (nullable = true)
-- Total_Population: integer (nullable = true)
-- Low_Income_Lone_Parent_Families: integer (nullable = true)
-- Average_Family_Income: integer (nullable = true)
-- Visible_Minority_Category: integer (nullable = true)
-- Not_Visible_Minority: integer (nullable = true)
-- Recent_Immigrants: integer (nullable = true)
-- College_Certificate/Diploma: integer (nullable = true)
-- Bachelor_Degree_or_Higher: integer (nullable = true)
-- Tenant_Average_Rent: integer (nullable = true)
-- Unemployed: integer (nullable = true)
-- Low_Income_Families: integer (nullable = true)
-- Total_Area: double (nullable = true)
-- amenitiesFeatures: vector (nullable = true)
-- property_type_indexed: double (nullable = false)
-- room_type_indexed: double (nullable = false)
-- bed_type_indexed: double (nullable = false)
-- cancellation_policy_indexed: double (nullable = false)
-- property_type_indexed_encoded: vector (nullable = true)
-- room_type_indexed_encoded: vector (nullable = true)
-- bed_type_indexed_encoded: vector (nullable = true)
-- cancellation_policy_indexed_encoded: vector (nullable = true)
-- features: vector (nullable = true)

In [21]:
final_airbnb = final_df.select(col("features"),col("price").alias("label"))

In [22]:
display(final_airbnb)

features label List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 469.00 List(0, 38, List(0, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 101.00 List(0, 38, List(2, 29, 32, 35), List(1.0, 1.0, 1.0, 1.0)) 67.00 List(0, 38, List(2, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 73.00 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 54.00 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 135.00 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 150.00 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 68.00 List(0, 38, List(5, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 110.00 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 119.00 List(0, 38, List(0, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 110.00 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 110.00 List(0, 38, List(0, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 105.00 List(0, 38, List(0, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 90.00 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 145.00 List(0, 38, List(1, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55.00 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 175.00 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 140.00 List(0, 38, List(3, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 350.00 List(0, 38, List(2, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 64.00 List(0, 38, List(2, 29, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 56.00 List(0, 38, List(7, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 145.00 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 145.00 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 107.00 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 145.00 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 145.00 List(0, 38, List(2, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 62.00 List(0, 38, List(3, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 230.00 List(0, 38, List(2, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 300.00 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 175.00 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 160.00 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55.00 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 102.00 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 250.00 List(0, 38, List(0, 29, 30, 36), List(1.0, 1.0, 1.0, 1.0)) 60.00 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 74.00 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 240.00 List(0, 38, List(0, 29, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 83.00 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 180.00 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 119.00 List(0, 38, List(3, 29, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 81.00 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 81.00 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 248.00 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 93.00 List(0, 38, List(0, 29, 31, 34), List(1.0, 1.0, 1.0, 1.0)) 99.00 List(0, 38, List(1, 30, 36), List(1.0, 1.0, 1.0)) 50.00 List(0, 38, List(2, 29, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 81.00 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 81.00 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 97.00 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 180.00 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 189.00 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 154.00 List(0, 38, List(4, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 115.00 List(0, 38, List(1, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 48.00 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 75.00 List(0, 38, List(5, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 60.00 List(0, 38, List(2, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 250.00 List(0, 38, List(8, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 87.00 List(0, 38, List(2, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 90.00 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 400.00 List(0, 38, List(3, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 3

In [23]:
final_airbnb.printSchema()

root
-- features: vector (nullable = true)
-- label: string (nullable = true)

In [24]:
def convert_dtype(df, colname,new_dtype):
  return(df.withColumn(colname, df[colname].cast(new_dtype)))

In [25]:
final_airbnb_df = convert_dtype(final_airbnb, "label", IntegerType())

In [26]:
final_airbnb_df.printSchema()

root
-- features: vector (nullable = true)
-- label: integer (nullable = true)

In [27]:
display(final_airbnb_df)

features label List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 469 List(0, 38, List(0, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 101 List(0, 38, List(2, 29, 32, 35), List(1.0, 1.0, 1.0, 1.0)) 67 List(0, 38, List(2, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 73 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 54 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 135 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 150 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 68 List(0, 38, List(5, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 110 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 119 List(0, 38, List(0, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 110 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 110 List(0, 38, List(0, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 105 List(0, 38, List(0, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 90 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 145 List(0, 38, List(1, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 175 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 140 List(0, 38, List(3, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 350 List(0, 38, List(2, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 64 List(0, 38, List(2, 29, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 56 List(0, 38, List(7, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 145 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 145 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 107 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 145 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 145 List(0, 38, List(2, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 62 List(0, 38, List(3, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 230 List(0, 38, List(2, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 300 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 175 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 160 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 102 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 250 List(0, 38, List(0, 29, 30, 36), List(1.0, 1.0, 1.0, 1.0)) 60 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 74 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 240 List(0, 38, List(0, 29, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 83 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 180 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 119 List(0, 38, List(3, 29, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 81 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 81 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 248 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 93 List(0, 38, List(0, 29, 31, 34), List(1.0, 1.0, 1.0, 1.0)) 99 List(0, 38, List(1, 30, 36), List(1.0, 1.0, 1.0)) 50 List(0, 38, List(2, 29, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 81 List(0, 38, List(1, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 81 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 97 List(0, 38, List(2, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 180 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 189 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 154 List(0, 38, List(4, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 115 List(0, 38, List(1, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 48 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 75 List(0, 38, List(5, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 60 List(0, 38, List(2, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 250 List(0, 38, List(8, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 87 List(0, 38, List(2, 29, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 90 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 400 List(0, 38, List(3, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 325 List(0, 38, List(0, 29, 30, 35), List(1.0, 1.0, 1.0, 1.0)) 119 List(0, 38, List(9, 28, 30, 36), List(1.0, 1.0, 1.0, 1.0)) 140 List(0, 38, List(0, 28, 30, 35), List(1.0, 1.0, 1.0

In [28]:
#######################Gradient Boosting modelling##############################

In [29]:
from pyspark.ml import Pipeline
from pyspark.ml.classification import GBTClassifier
from pyspark.ml.feature import StringIndexer, VectorIndexer
from pyspark.ml.evaluation import MulticlassClassificationEvaluator



# Split the data into training and test sets (30% held out for testing)
(trainingData, testData) = final_airbnb_df.randomSplit([0.8, 0.2])

print("Training Dataset Count: " + str(trainingData.count()))
print("Test Dataset Count: " + str(testData.count()))


Training Dataset Count: 15486
Test Dataset Count: 3935

In [30]:
final_airbnb_df = final_airbnb_df.na.fill(0) 

In [31]:
from pyspark.ml import Pipeline
from pyspark.ml.regression import GBTRegressor
from pyspark.ml.feature import VectorIndexer
from pyspark.ml.evaluation import RegressionEvaluator

# Automatically identify categorical features, and index them.
# Set maxCategories so features with > 4 distinct values are treated as continuous.
featuresCols = final_airbnb_df.columns
featuresCols.remove('label')
# This concatenates all feature columns into a single feature vector in a new column "rawFeatures".
vectorAssembler = VectorAssembler(inputCols=featuresCols, outputCol="rawFeatures")
# This identifies categorical features and indexes them.
vectorIndexer = VectorIndexer(inputCol="rawFeatures", outputCol="features", maxCategories=4)

gbt = GBTRegressor(labelCol="label")

paramGrid = ParamGridBuilder()\
  .addGrid(gbt.maxDepth, [2, 5])\
  .addGrid(gbt.maxIter, [10, 100])\
  .build()
# We define an evaluation metric.  This tells CrossValidator how well we are doing by comparing the true labels with predictions.
evaluator = RegressionEvaluator(metricName="rmse", labelCol=gbt.getLabelCol(), predictionCol=gbt.getPredictionCol())
# Declare the CrossValidator, which runs model tuning for us.
cv = CrossValidator(estimator=gbt, evaluator=evaluator, estimatorParamMaps=paramGrid)



In [32]:
pipeline = Pipeline(stages=[vectorAssembler, vectorIndexer, cv])

In [33]:
pipelineModel = pipeline.fit(trainingData)

--------------------------------------------------------------------------- 
 IllegalArgumentException Traceback (most recent call last)
 <command-3522504541062005> in <module> () 
 ----> 1 pipelineModel = pipeline . fit ( trainingData ) 

 /databricks/spark/python/pyspark/ml/base.py in fit (self, dataset, params) 
 130 return self . copy ( params ) . _fit ( dataset ) 
 131 else : 
 --> 132 return self . _fit ( dataset ) 
 133 else : 
 134 raise ValueError("Params must be either a param map or a list/tuple of param maps, "

 /databricks/spark/python/pyspark/ml/pipeline.py in _fit (self, dataset) 
 107 dataset = stage . transform ( dataset ) 
 108 else : # must be an Estimator 
 --> 109 model = stage . fit ( dataset ) 
 110 transformers . append ( model ) 
 111 if i < indexOfLastEstimator : 

 /databricks/spark/python/pyspark/ml/base.py in fit (self, dataset, params) 
 130 return self . copy ( params ) . _fit ( dataset ) 
 131 else : 
 --> 132 return self . _fit ( dataset ) 
 133 else : 
 134 raise ValueError("Params must be either a param map or a list/tuple of param maps, "

 /databricks/spark/python/pyspark/ml/wrapper.py in _fit (self, dataset) 
 293 
 294 def _fit ( self , dataset ) : 
 --> 295 java_model = self . _fit_java ( dataset ) 
 296 model = self . _create_model ( java_model ) 
 297 return self . _copyValues ( model ) 

 /databricks/spark/python/pyspark/ml/wrapper.py in _fit_java (self, dataset) 
 290 """
 291 self . _transfer_params_to_java ( ) 
 --> 292 return self . _java_obj . fit ( dataset . _jdf ) 
 293 
 294 def _fit ( self , dataset ) : 

 /databricks/spark/python/lib/py4j-0.10.7-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1255 answer = self . gateway_client . send_command ( command ) 
 1256 return_value = get_return_value(
 -> 1257 answer, self.gateway_client, self.target_id, self.name)
 1258 
 1259 for temp_arg in temp_args : 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 77 raise QueryExecutionException ( s . split ( ': ' , 1 ) [ 1 ] , stackTrace ) 
 78 if s . startswith ( 'java.lang.IllegalArgumentException: ' ) : 
 ---> 79 raise IllegalArgumentException ( s . split ( ': ' , 1 ) [ 1 ] , stackTrace ) 
 80 raise 
 81 return deco 

 IllegalArgumentException : 'requirement failed: Column features already exists.'

In [34]:

# Select example rows to display.
predictions.select("label", "features").show(5)

# Select (prediction, true label) and compute test error
evaluator = RegressionEvaluator(
    labelCol="label", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

gbtModel = model.stages[1]
print(gbtModel)  # summary only



+-----+--------------------+
label| features|
+-----+--------------------+
 332|(38,[0,28,30],[1....|
 30|(38,[0,28,30,34],...|
 35|(38,[0,28,30,34],...|
 40|(38,[0,28,30,34],...|
 43|(38,[0,28,30,34],...|
+-----+--------------------+
only showing top 5 rows

Root Mean Squared Error (RMSE) on test data = 103.937
GBTRegressionModel (uid=GBTRegressor_e08502d75d9c) with 2 trees

In [35]:
display(predictions)

features label indexedFeatures prediction List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 30 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 30 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 43 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 43 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 46 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 48 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 48 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 48 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 50 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 50 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 50 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 54 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 56 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 56 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 58 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 59 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 59 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 59 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 59 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 60 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 60 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 60 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 60 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(

In [36]:
#######################hyperparameter tuning################################

In [37]:
featureIndexer =\
    VectorIndexer(inputCol="features", outputCol="indexedFeatures", maxCategories=4).fit(final_airbnb_df)

# Split the data into training and test sets (30% held out for testing)
(trainingData, testData) = final_airbnb_df.randomSplit([0.7, 0.3])

# Train a GBT model.
gbt = GBTRegressor(featuresCol="indexedFeatures", maxIter=2)



In [38]:

from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
from pyspark.ml.evaluation import RegressionEvaluator
# Define a grid of hyperparameters to test:
#  - maxDepth: max depth of each decision tree in the GBT ensemble
#  - maxIter: iterations, i.e., number of trees in each GBT ensemble
# In this example notebook, we keep these values small.  In practice, to get the highest accuracy, you would likely want to try deeper trees (10 or higher) and more trees in the ensemble (>100).
paramGrid = ParamGridBuilder()\
  .addGrid(gbt.maxDepth, [2, 5])\
  .addGrid(gbt.maxIter, [10, 100])\
  .build()
# We define an evaluation metric.  This tells CrossValidator how well we are doing by comparing the true labels with predictions.
evaluator = RegressionEvaluator(metricName="rmse", labelCol=gbt.getLabelCol(), predictionCol=gbt.getPredictionCol())
# Declare the CrossValidator, which runs model tuning for us.
cv = CrossValidator(estimator=gbt, evaluator=evaluator, estimatorParamMaps=paramGrid)

In [39]:
from pyspark.ml import Pipeline
pipeline = Pipeline(stages=[featureIndexer, gbt])

In [40]:
pipelineModel = pipeline.fit(trainingData)

In [41]:
predictions = pipelineModel.transform(testData)

In [42]:
rmse = evaluator.evaluate(predictions)
print ("RMSE on our test set: %g", rmse)

RMSE on our test set: %g 94.49422501775405

In [43]:
display(predictions)

features label indexedFeatures prediction List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 30 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 30 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 43 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 43 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 46 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 48 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 48 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 48 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 50 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 50 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 50 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 54 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 55 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 56 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 56 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 58 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 59 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 59 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 59 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 59 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 60 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 60 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 60 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 60 List(0, 38, List(0, 28, 30, 34), List(1.0, 1.0, 1.0, 1.0)) 143.50782198584426 List(0, 38, List(0, 28, 30, 34), List(

In [44]:
import numpy as np

def smape(A, F):
    return 100/len(A) * np.sum(2 * np.abs(F - A) / (np.abs(A) + np.abs(F)))

# price is the column for the actual price of the listing
# prediction is the column for the predicted price of the listing
A = np.array(pred_results.select('price').collect())
F = np.array(pred_results.select('prediction').collect())

print(smape(A, F))

--------------------------------------------------------------------------- 
 NameError Traceback (most recent call last)
 <command-3522504541062000> in <module> () 
 6 # price is the column for the actual price of the listing 
 7 # prediction is the column for the predicted price of the listing 
 ----> 8 A = np . array ( pred_results . select ( 'price' ) . collect ( ) ) 
 9 F = np . array ( pred_results . select ( 'prediction' ) . collect ( ) ) 
 10 

 NameError : name 'pred_results' is not defined